In [321]:
try:
    __IPYTHON__
    USING_IPYTHON = True
    %load_ext autoreload
    %autoreload 2
except NameError:
    USING_IPYTHON = False

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


#### Argparse

In [322]:
import argparse
ap = argparse.ArgumentParser()
ap.add_argument('project_root', help='')
ap.add_argument('--mrp-data-dir', default='data', help='')
ap.add_argument('--mrp-test-dir', default='src/tests', help='')
ap.add_argument('--tests-fixtures-file-template', default='fixtures/{}-test.jsonl', help='')

ap.add_argument('--graphviz-sub-dir', default='visualization/graphviz', help='')
ap.add_argument('--train-sub-dir', default='training', help='')
ap.add_argument('--companion-sub-dir', default='companion')
ap.add_argument('--jamr-alignment-file', default='jamr.mrp')

ap.add_argument('--test-input-file', default='evaluation/input.mrp', help='')
ap.add_argument('--test-companion-file', default='evaluation/udpipe.mrp', help='')
ap.add_argument('--allennlp-mrp-json-file-template', default='allennlp-mrp-json-big-{}-{}.jsonl', help='')
ap.add_argument('--data-size-limit', type=int, default=10000, help='')

ap.add_argument('--mrp-file-extension', default='.mrp')
ap.add_argument('--companion-file-extension', default='.conllu')
ap.add_argument('--graphviz-file-template', default='http://localhost:8000/files/proj29_ds1/home/slai/mrp2019/visualization/graphviz/{}/{}.mrp/{}.png')
ap.add_argument('--parse-plot-file-template', default='http://localhost:8000/files/proj29_ds1/home/slai/mrp2019/visualization/graphviz/{}/{}.png')

ap.add_argument('--cuda-device', type=int, default=0)


arg_string = """
    /data/proj29_ds1/home/slai/mrp2019
"""
arguments = [arg for arg_line in arg_string.split(r'\\n') for arg in arg_line.split()]

In [3]:
if USING_IPYTHON:
    args = ap.parse_args(arguments)
else:
    args = ap.parse_args()

In [4]:
args

Namespace(allennlp_mrp_json_file_template='allennlp-mrp-json-big-{}-{}.jsonl', companion_file_extension='.conllu', companion_sub_dir='companion', cuda_device=0, data_size_limit=10000, graphviz_file_template='http://localhost:8000/files/proj29_ds1/home/slai/mrp2019/visualization/graphviz/{}/{}.mrp/{}.png', graphviz_sub_dir='visualization/graphviz', jamr_alignment_file='jamr.mrp', mrp_data_dir='data', mrp_file_extension='.mrp', mrp_test_dir='src/tests', parse_plot_file_template='http://localhost:8000/files/proj29_ds1/home/slai/mrp2019/visualization/graphviz/{}/{}.png', project_root='/data/proj29_ds1/home/slai/mrp2019', test_companion_file='evaluation/udpipe.mrp', test_input_file='evaluation/input.mrp', tests_fixtures_file_template='fixtures/{}-test.jsonl', train_sub_dir='training')

#### Library imports

In [5]:
import json
import logging
import os
import pprint
import re
import string
from collections import Counter, defaultdict, deque

import matplotlib.pyplot as plt
import networkx as nx
import numpy as np
import plot_util
import torch
from action_state import mrp_json2parser_states, _generate_parser_action_states
from action_state import ERROR, APPEND, RESOLVE, IGNORE
from preprocessing import (CompanionParseDataset, MrpDataset, JamrAlignmentDataset,
                           read_companion_parse_json_file, read_mrp_json_file, parse2parse_json)            
from torch import nn
from tqdm import tqdm

#### ipython notebook specific imports

In [6]:
if USING_IPYTHON:
    # matplotlib config
    %matplotlib inline

In [7]:
sh = logging.StreamHandler()
formatter = logging.Formatter('%(levelname)-8s [%(name)s:%(lineno)d] %(message)s')
sh.setFormatter(formatter)
logging.basicConfig(
    level=logging.DEBUG, 
    handlers=[sh]
)
mute_logger_names = ['allennlp.data.iterators.data_iterator']
for logger_name in mute_logger_names:
    logger = logging.getLogger(logger_name)  # pylint: disable=invalid-name
    logger.setLevel(logging.INFO)

logger = logging.getLogger(__name__)  # pylint: disable=invalid-name
logger.setLevel(logging.INFO)

### Constants

In [8]:
UNKWOWN = 'UNKWOWN'

### Load data

In [9]:
train_dir = os.path.join(args.project_root, args.mrp_data_dir, args.train_sub_dir)

In [10]:
mrp_dataset = MrpDataset()

In [11]:
frameworks, framework2dataset2mrp_jsons = mrp_dataset.load_mrp_json_dir(
    train_dir, args.mrp_file_extension)

frameworks: 100%|██████████| 5/5 [00:18<00:00,  3.19s/it]t/s]


In [12]:
framework2dataset2mrp_jsons.keys()

dict_keys(['ucca', 'psd', 'eds', 'dm', 'amr'])

### Data Preprocessing companion

In [13]:
companion_dir = os.path.join(args.project_root, args.mrp_data_dir, args.companion_sub_dir)

In [14]:
cparse_dataset = CompanionParseDataset()

In [15]:
dataset2cid2parse = cparse_dataset.load_companion_parse_dir(companion_dir, args.companion_file_extension)

INFO     [preprocessing:179] framework amr found
dataset: 100%|██████████| 13/13 [00:01<00:00,  9.95it/s]
INFO     [preprocessing:179] framework dm found
dataset: 100%|██████████| 5/5 [00:03<00:00,  1.19it/s]
INFO     [preprocessing:179] framework ucca found
dataset: 100%|██████████| 6/6 [00:00<00:00, 31.98it/s]


In [16]:
dataset2cid2parse_json = cparse_dataset.convert_parse2parse_json()

In [17]:
dataset2cid2parse.keys()

dict_keys(['amr-guidelines', 'bolt', 'cctv', 'dfa', 'dfb', 'fables', 'lorelei', 'mt09sdl', 'proxy', 'rte', 'wb', 'wiki', 'xinhua', 'wsj', 'ewt'])

In [18]:
# Some data is missing
'20003001' in dataset2cid2parse['wsj']

False

### Load JAMR alignment data

In [19]:
jalignment_dataset = JamrAlignmentDataset()

In [20]:
cid2alignment = jalignment_dataset.load_jamr_alignment_file(os.path.join(
    args.project_root,
    args.mrp_data_dir,
    args.companion_sub_dir,
    args.jamr_alignment_file
))

### Load testing data

In [21]:
test_input_filename = os.path.join(args.project_root, args.mrp_data_dir, args.test_input_file)
test_companion_filename = os.path.join(args.project_root, args.mrp_data_dir, args.test_companion_file)

In [22]:
test_mrp_jsons = read_mrp_json_file(test_input_filename)
test_parse_jsons = read_companion_parse_json_file(test_companion_filename)

In [23]:
parse_json = test_parse_jsons['102990']

In [24]:
mrp_json = framework2dataset2mrp_jsons['psd']['wsj'][1]

In [25]:
test_configs = [
    ('ucca', 'wiki', 70),
]
framework, dataset, idx = test_configs[0]

In [26]:
mrp_json = framework2dataset2mrp_jsons[framework][dataset][idx]
cid = mrp_json.get('id')

In [27]:
parse_json = dataset2cid2parse_json[dataset][cid]

In [28]:
doc = mrp_json['input']

In [29]:
doc

'In the final minute of the game, Johnson had the ball stolen by Celtics center Robert Parish, and then missed two free throws that could have won the game.'

In [30]:
token_pos = 0
anchors = []
char_pos2tokenized_parse_node_id = []

for node_id, node in enumerate(parse_json.get('nodes')):
    label = node.get('label')
    label_size = len(label)
    while doc[token_pos] == ' ':
        token_pos += 1
        char_pos2tokenized_parse_node_id.append(node_id)
    anchors.append((token_pos, token_pos + label_size))
    char_pos2tokenized_parse_node_id.extend([node_id] * (label_size))
    print(node_id, doc[token_pos: token_pos + label_size], anchors[-1], len(char_pos2tokenized_parse_node_id))
    token_pos += label_size

0 In (0, 2) 2
1 the (3, 6) 6
2 final (7, 12) 12
3 minute (13, 19) 19
4 of (20, 22) 22
5 the (23, 26) 26
6 game (27, 31) 31
7 , (31, 32) 32
8 Johnson (33, 40) 40
9 had (41, 44) 44
10 the (45, 48) 48
11 ball (49, 53) 53
12 stolen (54, 60) 60
13 by (61, 63) 63
14 Celtics (64, 71) 71
15 center (72, 78) 78
16 Robert (79, 85) 85
17 Parish (86, 92) 92
18 , (92, 93) 93
19 and (94, 97) 97
20 then (98, 102) 102
21 missed (103, 109) 109
22 two (110, 113) 113
23 free (114, 118) 118
24 throws (119, 125) 125
25 that (126, 130) 130
26 could (131, 136) 136
27 have (137, 141) 141
28 won (142, 145) 145
29 the (146, 149) 149
30 game (150, 154) 154
31 . (154, 155) 155


In [31]:
doc

'In the final minute of the game, Johnson had the ball stolen by Celtics center Robert Parish, and then missed two free throws that could have won the game.'

In [32]:
len(char_pos2tokenized_parse_node_id)

155

In [33]:
doc = mrp_json['input']

In [34]:
mrp_json['tops']

[34]

In [35]:
mrp_parser_states, mrp_meta_data = mrp_json2parser_states(
    mrp_json, 
    tokenized_parse_nodes=parse_json['nodes'],
)

In [36]:
(
    doc,
    nodes,
    node_id2node,
    edge_id2edge,
    top_oriented_edges,
    token_nodes,
    # abstract_node_id_set,
    parent_id2indegree,
    # parent_id2child_id_set,
    # child_id2parent_id_set,
    # child_id2edge_id_set,
    # parent_id2edge_id_set,
    # parent_child_id2edge_id_set,
    parse_nodes_anchors,
    char_pos2tokenized_node_id,
    curr_node_ids,
    token_states,
    actions,
) = mrp_meta_data

In [37]:
curr_node_ids = mrp_meta_data[-3]
token_states = mrp_meta_data[-2]
actions = mrp_meta_data[-1]

In [38]:
*_, curr_node_ids, token_states, actions = mrp_meta_data

In [39]:
actions[1]

(1,
 (1,
  0,
  {'id': 0,
   'anchors': [{'from': 0, 'to': 2}],
   'label': 'In',
   'propagate_label': 'R'},
  [[]]))

In [40]:
actions[-4:]

[(1,
  (3,
   2,
   {'id': 41, 'propagate_label': 'A'},
   [[{'source': 41,
      'target': 28,
      'label': 'E',
      'id': 15,
      'parent': 41,
      'child': 28}],
    [{'source': 41,
      'target': 29,
      'label': 'C',
      'id': 24,
      'parent': 41,
      'child': 29}],
    [{'source': 41,
      'target': 30,
      'label': 'U',
      'id': 17,
      'parent': 41,
      'child': 30}]])),
 (1,
  (4,
   3,
   {'id': 40, 'propagate_label': 'H'},
   [[{'source': 40,
      'target': 25,
      'label': 'D',
      'id': 40,
      'parent': 40,
      'child': 25}],
    [{'source': 40,
      'target': 26,
      'label': 'F',
      'id': 32,
      'parent': 40,
      'child': 26}],
    [{'source': 40,
      'target': 27,
      'label': 'P',
      'id': 2,
      'parent': 40,
      'child': 27}],
    [{'source': 40,
      'target': 41,
      'label': 'A',
      'id': 16,
      'parent': 40,
      'child': 41}]])),
 (1,
  (3,
   2,
   {'id': 39, 'propagate_label': 'H'},
   [[{'s

In [41]:
for curr_node_id, action, token_state in zip(curr_node_ids, actions, token_states):
    action_type, params = action
#     pprint.pprint((curr_node_id, action[0]))
#     pprint.pprint(([token_group[:4] for token_group in token_state]))
    pprint.pprint((curr_node_id, action[0], [token_group[:5] for token_group in token_state]))

(0, 0, [(0, False, 'In', [])])
(1, 1, [(0, True, 'R', [(0, False, 'In', [])])])
(1, 0, [(0, True, 'R', [(0, False, 'In', [])]), (1, False, 'the', [])])
(2,
 1,
 [(0, True, 'R', [(0, False, 'In', [])]),
  (1, True, 'E', [(1, False, 'the', [])])])
(2,
 0,
 [(0, True, 'R', [(0, False, 'In', [])]),
  (1, True, 'E', [(1, False, 'the', [])]),
  (2, False, 'final', [])])
(3,
 1,
 [(0, True, 'R', [(0, False, 'In', [])]),
  (1, True, 'E', [(1, False, 'the', [])]),
  (2, True, 'E', [(2, False, 'final', [])])])
(3,
 0,
 [(0, True, 'R', [(0, False, 'In', [])]),
  (1, True, 'E', [(1, False, 'the', [])]),
  (2, True, 'E', [(2, False, 'final', [])]),
  (3, False, 'minute', [])])
(4,
 1,
 [(0, True, 'R', [(0, False, 'In', [])]),
  (1, True, 'E', [(1, False, 'the', [])]),
  (2, True, 'E', [(2, False, 'final', [])]),
  (3, True, 'C', [(3, False, 'minute', [])])])
(4,
 1,
 [(32,
   True,
   'E',
   [(0, True, 'R', [(0, False, 'In', [])]),
    (1, True, 'E', [(1, False, 'the', [])]),
    (2, True, 'E', [(

  (24, True, 'P', [(24, False, 'throws', [])])])
(25,
 1,
 [(37,
   True,
   'H',
   [(33,
     True,
     'T',
     [(32,
       True,
       'E',
       [(0, True, 'R', [(0, False, 'In', [])]),
        (1, True, 'E', [(1, False, 'the', [])]),
        (2, True, 'E', [(2, False, 'final', [])]),
        (3, True, 'C', [(3, False, 'minute', [])])]),
      (4, True, 'R', [(4, False, 'of', [])]),
      (5, True, 'E', [(5, False, 'the', [])]),
      (6, True, 'C', [(6, False, 'game', [])])]),
    (7, True, 'U', [(7, False, ',', [])]),
    (8, True, 'A', [(8, False, 'Johnson', [])]),
    (9, True, 'F', [(9, False, 'had', [])]),
    (34,
     True,
     'A',
     [(10, True, 'E', [(10, False, 'the', [])]),
      (11, True, 'C', [(11, False, 'ball', [])])]),
    (12, True, 'P', [(12, False, 'stolen', [])]),
    (36,
     True,
     'A',
     [(13, True, 'R', [(13, False, 'by', [])]),
      (35,
       True,
       'E',
       [(14, True, 'A', [(14, False, 'Celtics', [])]),
        (15, True, '

In [42]:
for curr_node_id, action, token_state in zip(curr_node_ids, actions, [[]] + token_states):
    action_type, params = action
    pprint.pprint((curr_node_id, action[0], (action[1] or [None])[:2], [token_group[:4] for token_group in token_state]))
    

(0, 0, [None], [])
(1, 1, (1, 0), [(0, False, 'In', [])])
(1, 0, [None], [(0, True, 'R', [(0, False, 'In', [])])])
(2, 1, (1, 0), [(0, True, 'R', [(0, False, 'In', [])]), (1, False, 'the', [])])
(2,
 0,
 [None],
 [(0, True, 'R', [(0, False, 'In', [])]),
  (1, True, 'E', [(1, False, 'the', [])])])
(3,
 1,
 (1, 0),
 [(0, True, 'R', [(0, False, 'In', [])]),
  (1, True, 'E', [(1, False, 'the', [])]),
  (2, False, 'final', [])])
(3,
 0,
 [None],
 [(0, True, 'R', [(0, False, 'In', [])]),
  (1, True, 'E', [(1, False, 'the', [])]),
  (2, True, 'E', [(2, False, 'final', [])])])
(4,
 1,
 (1, 0),
 [(0, True, 'R', [(0, False, 'In', [])]),
  (1, True, 'E', [(1, False, 'the', [])]),
  (2, True, 'E', [(2, False, 'final', [])]),
  (3, False, 'minute', [])])
(4,
 1,
 (4, 3),
 [(0, True, 'R', [(0, False, 'In', [])]),
  (1, True, 'E', [(1, False, 'the', [])]),
  (2, True, 'E', [(2, False, 'final', [])]),
  (3, True, 'C', [(3, False, 'minute', [])])])
(4,
 0,
 [None],
 [(32,
   True,
   'E',
   [(0, True,

(12,
 0,
 [None],
 [(33,
   True,
   'T',
   [(32,
     True,
     'E',
     [(0, True, 'R', [(0, False, 'In', [])]),
      (1, True, 'E', [(1, False, 'the', [])]),
      (2, True, 'E', [(2, False, 'final', [])]),
      (3, True, 'C', [(3, False, 'minute', [])])]),
    (4, True, 'R', [(4, False, 'of', [])]),
    (5, True, 'E', [(5, False, 'the', [])]),
    (6, True, 'C', [(6, False, 'game', [])])]),
  (7, True, 'U', [(7, False, ',', [])]),
  (8, True, 'A', [(8, False, 'Johnson', [])]),
  (9, True, 'F', [(9, False, 'had', [])]),
  (34,
   True,
   'A',
   [(10, True, 'E', [(10, False, 'the', [])]),
    (11, True, 'C', [(11, False, 'ball', [])])])])
(13,
 1,
 (1, 0),
 [(33,
   True,
   'T',
   [(32,
     True,
     'E',
     [(0, True, 'R', [(0, False, 'In', [])]),
      (1, True, 'E', [(1, False, 'the', [])]),
      (2, True, 'E', [(2, False, 'final', [])]),
      (3, True, 'C', [(3, False, 'minute', [])])]),
    (4, True, 'R', [(4, False, 'of', [])]),
    (5, True, 'E', [(5, False, 'th

       'E',
       [(14, True, 'A', [(14, False, 'Celtics', [])]),
        (15, True, 'S', [(15, False, 'center', [])])]),
      (16, True, 'C', [(16, False, 'Robert', [])])])]),
  (18, True, 'U', [(18, False, ',', [])]),
  (19, True, 'L', [(19, False, 'and', [])]),
  (20, True, 'L', [(20, False, 'then', [])]),
  (21, True, 'D', [(21, False, 'missed', [])]),
  (22, True, 'D', [(22, False, 'two', [])]),
  (23, True, 'D', [(23, False, 'free', [])]),
  (24, True, 'P', [(24, False, 'throws', [])])])
(25,
 0,
 [None],
 [(37,
   True,
   'H',
   [(33,
     True,
     'T',
     [(32,
       True,
       'E',
       [(0, True, 'R', [(0, False, 'In', [])]),
        (1, True, 'E', [(1, False, 'the', [])]),
        (2, True, 'E', [(2, False, 'final', [])]),
        (3, True, 'C', [(3, False, 'minute', [])])]),
      (4, True, 'R', [(4, False, 'of', [])]),
      (5, True, 'E', [(5, False, 'the', [])]),
      (6, True, 'C', [(6, False, 'game', [])])]),
    (7, True, 'U', [(7, False, ',', [])]),
   

 [(37,
   True,
   'H',
   [(33,
     True,
     'T',
     [(32,
       True,
       'E',
       [(0, True, 'R', [(0, False, 'In', [])]),
        (1, True, 'E', [(1, False, 'the', [])]),
        (2, True, 'E', [(2, False, 'final', [])]),
        (3, True, 'C', [(3, False, 'minute', [])])]),
      (4, True, 'R', [(4, False, 'of', [])]),
      (5, True, 'E', [(5, False, 'the', [])]),
      (6, True, 'C', [(6, False, 'game', [])])]),
    (7, True, 'U', [(7, False, ',', [])]),
    (8, True, 'A', [(8, False, 'Johnson', [])]),
    (9, True, 'F', [(9, False, 'had', [])]),
    (34,
     True,
     'A',
     [(10, True, 'E', [(10, False, 'the', [])]),
      (11, True, 'C', [(11, False, 'ball', [])])]),
    (12, True, 'P', [(12, False, 'stolen', [])]),
    (36,
     True,
     'A',
     [(13, True, 'R', [(13, False, 'by', [])]),
      (35,
       True,
       'E',
       [(14, True, 'A', [(14, False, 'Celtics', [])]),
        (15, True, 'S', [(15, False, 'center', [])])]),
      (16, True, 'C', 

In [43]:
actions

[(0, None),
 (1,
  (1,
   0,
   {'id': 0,
    'anchors': [{'from': 0, 'to': 2}],
    'label': 'In',
    'propagate_label': 'R'},
   [[]])),
 (0, None),
 (1,
  (1,
   0,
   {'id': 1,
    'anchors': [{'from': 3, 'to': 6}],
    'label': 'the',
    'propagate_label': 'E'},
   [[]])),
 (0, None),
 (1,
  (1,
   0,
   {'id': 2,
    'anchors': [{'from': 7, 'to': 12}],
    'label': 'final',
    'propagate_label': 'E'},
   [[]])),
 (0, None),
 (1,
  (1,
   0,
   {'id': 3,
    'anchors': [{'from': 13, 'to': 19}],
    'label': 'minute',
    'propagate_label': 'C'},
   [[]])),
 (1,
  (4,
   3,
   {'id': 31, 'propagate_label': 'E'},
   [[{'source': 31,
      'target': 0,
      'label': 'R',
      'id': 31,
      'parent': 31,
      'child': 0}],
    [{'source': 31,
      'target': 1,
      'label': 'E',
      'id': 28,
      'parent': 31,
      'child': 1}],
    [{'source': 31,
      'target': 2,
      'label': 'E',
      'id': 21,
      'parent': 31,
      'child': 2}],
    [{'source': 31,
      't

In [44]:
token_states[1]

[(0, True, 'R', [(0, False, 'In', [])])]

In [45]:
[n['label'] for n in parse_json['nodes']]

['In',
 'the',
 'final',
 'minute',
 'of',
 'the',
 'game',
 ',',
 'Johnson',
 'had',
 'the',
 'ball',
 'stolen',
 'by',
 'Celtics',
 'center',
 'Robert',
 'Parish',
 ',',
 'and',
 'then',
 'missed',
 'two',
 'free',
 'throws',
 'that',
 'could',
 'have',
 'won',
 'the',
 'game',
 '.']

In [46]:
token_states[-1]

[(42,
  True,
  '<UCCA-TOP-NODE>',
  [(37,
    True,
    'H',
    [(33,
      True,
      'T',
      [(32,
        True,
        'E',
        [(0, True, 'R', [(0, False, 'In', [])]),
         (1, True, 'E', [(1, False, 'the', [])]),
         (2, True, 'E', [(2, False, 'final', [])]),
         (3, True, 'C', [(3, False, 'minute', [])])]),
       (4, True, 'R', [(4, False, 'of', [])]),
       (5, True, 'E', [(5, False, 'the', [])]),
       (6, True, 'C', [(6, False, 'game', [])])]),
     (7, True, 'U', [(7, False, ',', [])]),
     (8, True, 'A', [(8, False, 'Johnson', [])]),
     (9, True, 'F', [(9, False, 'had', [])]),
     (34,
      True,
      'A',
      [(10, True, 'E', [(10, False, 'the', [])]),
       (11, True, 'C', [(11, False, 'ball', [])])]),
     (12, True, 'P', [(12, False, 'stolen', [])]),
     (36,
      True,
      'A',
      [(13, True, 'R', [(13, False, 'by', [])]),
       (35,
        True,
        'E',
        [(14, True, 'A', [(14, False, 'Celtics', [])]),
         (

In [47]:
companion_parser_states, companion_meta_data = mrp_json2parser_states(
    parse_json,
    mrp_doc=doc,
    tokenized_parse_nodes=parse_json['nodes'],
)

In [48]:
logger.info(args.graphviz_file_template.format(
    framework, dataset, cid))

INFO     [__main__:2] http://localhost:8000/files/proj29_ds1/home/slai/mrp2019/visualization/graphviz/ucca/wiki.mrp/470004.png


In [49]:
mrp_json['input']

'In the final minute of the game, Johnson had the ball stolen by Celtics center Robert Parish, and then missed two free throws that could have won the game.'

In [50]:
mrp_parser_states

[(0,
  [(0, None),
   (1,
    (1,
     0,
     {'id': 0,
      'anchors': [{'from': 0, 'to': 2}],
      'label': 'In',
      'propagate_label': 'R'},
     [[]]))],
  [],
  [],
  [],
  [(0, 0, [(0, 0, None)])],
  [(0, True, 'R', [(0, False, 'In', 'In')])]),
 (1,
  [(0, None),
   (1,
    (1,
     0,
     {'id': 1,
      'anchors': [{'from': 3, 'to': 6}],
      'label': 'the',
      'propagate_label': 'E'},
     [[]]))],
  [],
  [],
  [],
  [(0, 0, [(0, 0, None)]), (1, 1, [(1, 1, None)])],
  [(0, True, 'R', [(0, False, 'In', 'In')]),
   (1, True, 'E', [(1, False, 'the', 'the')])]),
 (2,
  [(0, None),
   (1,
    (1,
     0,
     {'id': 2,
      'anchors': [{'from': 7, 'to': 12}],
      'label': 'final',
      'propagate_label': 'E'},
     [[]]))],
  [],
  [],
  [],
  [(0, 0, [(0, 0, None)]), (1, 1, [(1, 1, None)]), (2, 2, [(2, 2, None)])],
  [(0, True, 'R', [(0, False, 'In', 'In')]),
   (1, True, 'E', [(1, False, 'the', 'the')]),
   (2, True, 'E', [(2, False, 'final', 'final')])]),
 (3,
  

In [51]:
[(node['id'], node.get('label')) for node in mrp_json['nodes']]

[(0, 'In'),
 (1, 'the'),
 (2, 'final'),
 (3, 'minute'),
 (4, 'of'),
 (5, 'the'),
 (6, 'game'),
 (7, ','),
 (8, 'Johnson'),
 (9, 'had'),
 (10, 'the'),
 (11, 'ball'),
 (12, 'stolen'),
 (13, 'by'),
 (14, 'Celtics'),
 (15, 'center'),
 (16, 'RobertParish'),
 (17, ','),
 (18, 'and'),
 (19, 'then'),
 (20, 'missed'),
 (21, 'two'),
 (22, 'free'),
 (23, 'throws'),
 (24, 'that'),
 (25, 'could'),
 (26, 'have'),
 (27, 'won'),
 (28, 'the'),
 (29, 'game'),
 (30, '.'),
 (31, None),
 (32, None),
 (33, None),
 (34, None),
 (35, None),
 (36, None),
 (37, None),
 (38, None),
 (39, None),
 (40, None),
 (41, None)]

In [52]:
doc

'In the final minute of the game, Johnson had the ball stolen by Celtics center Robert Parish, and then missed two free throws that could have won the game.'

In [53]:
parse_json['nodes']

[{'id': 0,
  'label': 'In',
  'properties': ['lemma', 'upos', 'xpos'],
  'values': ['in', 'ADP', 'IN']},
 {'id': 1,
  'label': 'the',
  'properties': ['lemma', 'upos', 'xpos'],
  'values': ['the', 'DET', 'DT']},
 {'id': 2,
  'label': 'final',
  'properties': ['lemma', 'upos', 'xpos'],
  'values': ['final', 'ADJ', 'JJ']},
 {'id': 3,
  'label': 'minute',
  'properties': ['lemma', 'upos', 'xpos'],
  'values': ['minute', 'NOUN', 'NN']},
 {'id': 4,
  'label': 'of',
  'properties': ['lemma', 'upos', 'xpos'],
  'values': ['of', 'ADP', 'IN']},
 {'id': 5,
  'label': 'the',
  'properties': ['lemma', 'upos', 'xpos'],
  'values': ['the', 'DET', 'DT']},
 {'id': 6,
  'label': 'game',
  'properties': ['lemma', 'upos', 'xpos'],
  'values': ['game', 'NOUN', 'NN']},
 {'id': 7,
  'label': ',',
  'properties': ['lemma', 'upos', 'xpos'],
  'values': [',', 'PUNCT', ',']},
 {'id': 8,
  'label': 'Johnson',
  'properties': ['lemma', 'upos', 'xpos'],
  'values': ['Johnson', 'PROPN', 'NNP']},
 {'id': 9,
  'label

In [54]:
[(node['id'], node['label']) for node in parse_json['nodes']]

[(0, 'In'),
 (1, 'the'),
 (2, 'final'),
 (3, 'minute'),
 (4, 'of'),
 (5, 'the'),
 (6, 'game'),
 (7, ','),
 (8, 'Johnson'),
 (9, 'had'),
 (10, 'the'),
 (11, 'ball'),
 (12, 'stolen'),
 (13, 'by'),
 (14, 'Celtics'),
 (15, 'center'),
 (16, 'Robert'),
 (17, 'Parish'),
 (18, ','),
 (19, 'and'),
 (20, 'then'),
 (21, 'missed'),
 (22, 'two'),
 (23, 'free'),
 (24, 'throws'),
 (25, 'that'),
 (26, 'could'),
 (27, 'have'),
 (28, 'won'),
 (29, 'the'),
 (30, 'game'),
 (31, '.')]

In [55]:
anchors

[(0, 2),
 (3, 6),
 (7, 12),
 (13, 19),
 (20, 22),
 (23, 26),
 (27, 31),
 (31, 32),
 (33, 40),
 (41, 44),
 (45, 48),
 (49, 53),
 (54, 60),
 (61, 63),
 (64, 71),
 (72, 78),
 (79, 85),
 (86, 92),
 (92, 93),
 (94, 97),
 (98, 102),
 (103, 109),
 (110, 113),
 (114, 118),
 (119, 125),
 (126, 130),
 (131, 136),
 (137, 141),
 (142, 145),
 (146, 149),
 (150, 154),
 (154, 155)]

### Create training instance

In [323]:
# framework = 'ucca'
# ignore_framework_set = {'amr', 'dm', 'psd', 'eds'}
# dataset = 'wiki'
# ignore_dataset_set = {}

framework = 'dm'
ignore_framework_set = {'amr', 'ucca', 'psd', 'eds'}
dataset = 'wsj'
ignore_dataset_set = {}

# framework = 'ucca'
# ignore_framework_set = {'amr', 'psd', 'eds'}
# dataset = 'wiki'
# ignore_dataset_set = {}

In [324]:
frameworks

['ucca', 'psd', 'eds', 'dm', 'amr']

In [325]:
framework_names = '-'.join([
    framework 
    for framework in frameworks 
    if framework not in ignore_framework_set
])
framework_names

'dm'

In [326]:
allennlp_tests_fixtures_output_file = os.path.join(
    args.project_root, args.mrp_test_dir, args.tests_fixtures_file_template.format(framework_names))

allennlp_framework_train_output_file = os.path.join(
    args.project_root, args.allennlp_mrp_json_file_template.format(framework_names, 'train'))

allennlp_framework_test_output_file = os.path.join(
    args.project_root, args.allennlp_mrp_json_file_template.format(framework_names, 'test'))

In [328]:
# Create tests fixture jsonl
fixture_combinations = [
#     ('ucca', 'wiki', 70),
    ('dm', 'wsj', 3)
] * 5

with open(allennlp_tests_fixtures_output_file, 'w') as wf:
    for framework, dataset, idx in fixture_combinations:
        mrp_json = framework2dataset2mrp_jsons[framework][dataset][idx]
        cid = mrp_json.get('id')
        doc = mrp_json.get('input')
        
        alignment = {}
        if framework == 'amr':
            alignment = cid2alignment[cid]  
        parse_json = dataset2cid2parse_json.get(dataset, {}).get(cid, {})

        if parse_json:
            mrp_parser_states, mrp_meta_data = mrp_json2parser_states(
                mrp_json, 
                tokenized_parse_nodes=parse_json['nodes'],
                alignment=alignment,
            )
            companion_parser_states, companion_meta_data = mrp_json2parser_states(
                parse_json, 
                mrp_doc=doc,
                tokenized_parse_nodes=parse_json['nodes'],
            )

            data_instance = {
                'mrp_json': mrp_json,
                'parse_json': parse_json,
                'mrp_parser_states': mrp_parser_states,
                'mrp_meta_data': mrp_meta_data,
                'companion_parser_states': companion_parser_states,
                'companion_meta_data': companion_meta_data,
            }
            json_encoded_instance = json.dumps(data_instance)
            wf.write(json_encoded_instance + '\n')

In [329]:
for idx in range(20):
    mrp_json = framework2dataset2mrp_jsons[framework][dataset][idx]
    cid = mrp_json.get('id')
    if cid in dataset2cid2parse[dataset]:
        print(idx)

3
8
13
18


In [330]:
[state[-1] for state in mrp_parser_states]

[[(0, True, 'the', [(0, False, 'the', 'The')])],
 [(0, True, 'the', [(0, False, 'the', 'The')]),
  (1, True, 'asbestos', [(1, False, 'asbestos', 'asbestos')])],
 [(0, True, 'the', [(0, False, 'the', 'The')]),
  (1, True, 'asbestos', [(1, False, 'asbestos', 'asbestos')]),
  (2, False, 'fiber', 'fiber')],
 [(0, True, 'the', [(0, False, 'the', 'The')]),
  (1, True, 'asbestos', [(1, False, 'asbestos', 'asbestos')]),
  (2, False, 'fiber', 'fiber'),
  (4, True, 'crocidolite', [(4, False, 'crocidolite', 'crocidolite')])],
 [(2,
   True,
   'fiber',
   [(0, True, 'the', [(0, False, 'the', 'The')]),
    (1, True, 'asbestos', [(1, False, 'asbestos', 'asbestos')]),
    (2, False, 'fiber', 'fiber'),
    (4, True, 'crocidolite', [(4, False, 'crocidolite', 'crocidolite')])])],
 [(2,
   True,
   'fiber',
   [(0, True, 'the', [(0, False, 'the', 'The')]),
    (1, True, 'asbestos', [(1, False, 'asbestos', 'asbestos')]),
    (2, False, 'fiber', 'fiber'),
    (4, True, 'crocidolite', [(4, False, 'crocidol

In [331]:
mrp_meta_data[-1]

[(0, None),
 (1,
  (1,
   0,
   {'id': 0,
    'label': 'the',
    'properties': ['pos', 'frame'],
    'values': ['DT', 'q:i-h-h'],
    'anchors': [{'from': 0, 'to': 3}]},
   [[]])),
 (0, None),
 (1,
  (1,
   0,
   {'id': 1,
    'label': 'asbestos',
    'properties': ['pos', 'frame'],
    'values': ['NN', 'n:x'],
    'anchors': [{'from': 4, 'to': 12}]},
   [[]])),
 (0, None),
 (2, None),
 (0, None),
 (1,
  (1,
   0,
   {'id': 4,
    'label': 'crocidolite',
    'properties': ['pos', 'frame'],
    'values': ['NN', 'n:x'],
    'anchors': [{'from': 20, 'to': 31}]},
   [[]])),
 (1,
  (4,
   2,
   {'id': 2,
    'label': 'fiber',
    'properties': ['pos', 'frame'],
    'values': ['NN', 'n:x'],
    'anchors': [{'from': 13, 'to': 18}]},
   [[{'source': 0,
      'target': 2,
      'label': 'BV',
      'id': 2,
      'parent': 2,
      'child': 0}],
    [{'source': 1,
      'target': 2,
      'label': 'compound',
      'id': 1,
      'parent': 2,
      'child': 1}],
    [],
    [{'source': 4,
    

In [332]:
doc

'The asbestos fiber, crocidolite, is unusually resilient once it enters the lungs, with even brief exposures to it causing symptoms that show up decades later, researchers said.'

In [333]:
parse_json

{'id': '20003002',
 'tops': [30],
 'nodes': [{'id': 0,
   'label': 'The',
   'properties': ['lemma', 'upos', 'xpos'],
   'values': ['the', 'DET', 'DT']},
  {'id': 1,
   'label': 'asbestos',
   'properties': ['lemma', 'upos', 'xpos'],
   'values': ['asbestos', 'NOUN', 'NN']},
  {'id': 2,
   'label': 'fiber',
   'properties': ['lemma', 'upos', 'xpos'],
   'values': ['fiber', 'NOUN', 'NN']},
  {'id': 3,
   'label': ',',
   'properties': ['lemma', 'upos', 'xpos'],
   'values': [',', 'PUNCT', ',']},
  {'id': 4,
   'label': 'crocidolite',
   'properties': ['lemma', 'upos', 'xpos'],
   'values': ['crocidolite', 'NOUN', 'NN']},
  {'id': 5,
   'label': ',',
   'properties': ['lemma', 'upos', 'xpos'],
   'values': [',', 'PUNCT', ',']},
  {'id': 6,
   'label': 'is',
   'properties': ['lemma', 'upos', 'xpos'],
   'values': ['be', 'VERB', 'VBZ']},
  {'id': 7,
   'label': 'unusually',
   'properties': ['lemma', 'upos', 'xpos'],
   'values': ['unusually', 'ADV', 'RB']},
  {'id': 8,
   'label': 'resil

In [334]:
[n['values'][2] for n in parse_json['nodes']]

['DT',
 'NN',
 'NN',
 ',',
 'NN',
 ',',
 'VBZ',
 'RB',
 'JJ',
 'IN',
 'PRP',
 'VBZ',
 'DT',
 'NNS',
 ',',
 'IN',
 'RB',
 'JJ',
 'NNS',
 'TO',
 'PRP',
 'VBG',
 'NNS',
 'WDT',
 'VBP',
 'RP',
 'NNS',
 'RB',
 ',',
 'NNS',
 'VBD',
 '.']

In [335]:
# Create train jsonl
if os.path.isfile(allennlp_framework_train_output_file) and os.path.isfile(
    allennlp_framework_train_output_file):
    logger.info('allennlp_train_output_file found, stop generation')
else:
#     pass
# if 1==1:
    data_size = 0
    with open(allennlp_framework_train_output_file, 'w') as train_wf:
        with open(allennlp_framework_test_output_file, 'w') as test_wf:
            for _, dataset, idx, mrp_json in tqdm(mrp_dataset.mrp_json_generator(
                ignore_framework_set=ignore_framework_set,
                ignore_dataset_set=ignore_dataset_set,
                data_size_limit=args.data_size_limit * 2
            )):
                cid = mrp_json.get('id')
                doc = mrp_json.get('input')

                framework = mrp_json.get('framework')
                alignment = {}
                if framework == 'amr':
                    alignment = cid2alignment[cid]  
                parse_json = dataset2cid2parse_json.get(dataset, {}).get(cid, {})

                if parse_json:
                    mrp_parser_states, mrp_meta_data = mrp_json2parser_states(
                        mrp_json, 
                        tokenized_parse_nodes=parse_json['nodes'],
                        alignment=alignment,
                    )
                    companion_parser_states, companion_meta_data = mrp_json2parser_states(
                        parse_json, 
                        mrp_doc=doc,
                        tokenized_parse_nodes=parse_json['nodes'],
                    )

                    # Continue if error
                    if not mrp_parser_states:
                        continue

                    data_instance = {
                        'mrp_json': mrp_json,
                        'parse_json': parse_json,
                        'mrp_parser_states': mrp_parser_states,
                        'mrp_meta_data': mrp_meta_data,
                        'companion_parser_states': companion_parser_states,
                        'companion_meta_data': companion_meta_data,
                    }
                    json_encoded_instance = json.dumps(data_instance)
                    if idx <= args.data_size_limit:
                        train_wf.write(json_encoded_instance + '\n')
                    else:
                        test_wf.write(json_encoded_instance + '\n')

62it [00:01, 42.76it/s]WARNING  [action_state:220] No top node provided
94it [00:01, 60.20it/s]WARNING  [action_state:516] pop empty node_state
106it [00:02, 57.21it/s]WARNING  [action_state:516] pop empty node_state
114it [00:02, 61.39it/s]WARNING  [action_state:516] pop empty node_state
122it [00:02, 57.07it/s]WARNING  [action_state:516] pop empty node_state
WARNING  [action_state:516] pop empty node_state
129it [00:02, 57.83it/s]WARNING  [action_state:516] pop empty node_state
159it [00:02, 53.21it/s]WARNING  [action_state:516] pop empty node_state
178it [00:03, 62.72it/s]WARNING  [action_state:516] pop empty node_state
188it [00:03, 67.90it/s]WARNING  [action_state:516] pop empty node_state
196it [00:03, 61.85it/s]WARNING  [action_state:516] pop empty node_state
232it [00:04, 33.55it/s]WARNING  [action_state:516] pop empty node_state
273it [00:05, 40.48it/s]WARNING  [action_state:516] pop empty node_state
293it [00:05, 40.18it/s]WARNING  [action_state:516] pop empty node_state
302i

3034it [01:00, 46.46it/s]WARNING  [action_state:516] pop empty node_state
3057it [01:00, 34.26it/s]WARNING  [action_state:516] pop empty node_state
3063it [01:01, 33.58it/s]WARNING  [action_state:516] pop empty node_state
3091it [01:01, 48.24it/s]WARNING  [action_state:516] pop empty node_state
3104it [01:01, 52.89it/s]WARNING  [action_state:516] pop empty node_state
WARNING  [action_state:516] pop empty node_state
3114it [01:01, 52.67it/s]WARNING  [action_state:516] pop empty node_state
3131it [01:02, 50.70it/s]WARNING  [action_state:516] pop empty node_state
WARNING  [action_state:516] pop empty node_state
3148it [01:02, 48.71it/s]WARNING  [action_state:516] pop empty node_state
3168it [01:02, 52.65it/s]WARNING  [action_state:516] pop empty node_state
3211it [01:03, 51.82it/s]WARNING  [action_state:516] pop empty node_state
3228it [01:04, 26.93it/s]WARNING  [action_state:516] pop empty node_state
3256it [01:05, 25.52it/s]WARNING  [action_state:516] pop empty node_state
WARNING  [acti

5406it [01:55, 51.00it/s]WARNING  [action_state:516] pop empty node_state
5441it [01:56, 71.18it/s]WARNING  [action_state:516] pop empty node_state
5451it [01:56, 51.07it/s]WARNING  [action_state:516] pop empty node_state
5461it [01:56, 54.18it/s]WARNING  [action_state:516] pop empty node_state
5479it [01:57, 41.76it/s]WARNING  [action_state:516] pop empty node_state
5493it [01:57, 44.65it/s]WARNING  [action_state:516] pop empty node_state
5571it [01:58, 58.12it/s]WARNING  [action_state:516] pop empty node_state
WARNING  [action_state:516] pop empty node_state
5620it [01:59, 35.59it/s]WARNING  [action_state:516] pop empty node_state
5631it [01:59, 43.76it/s]WARNING  [action_state:516] pop empty node_state
5638it [01:59, 46.50it/s]WARNING  [action_state:516] pop empty node_state
5669it [02:00, 34.48it/s]WARNING  [action_state:516] pop empty node_state
5685it [02:01, 39.08it/s]WARNING  [action_state:516] pop empty node_state
5694it [02:01, 34.35it/s]WARNING  [action_state:516] pop empty 

8550it [03:00, 44.26it/s]WARNING  [action_state:516] pop empty node_state
8586it [03:00, 60.31it/s]WARNING  [action_state:516] pop empty node_state
8607it [03:01, 54.50it/s]WARNING  [action_state:516] pop empty node_state
8629it [03:01, 37.44it/s]WARNING  [action_state:516] pop empty node_state
8634it [03:01, 38.86it/s]WARNING  [action_state:516] pop empty node_state
8690it [03:03, 34.99it/s]WARNING  [action_state:516] pop empty node_state
8700it [03:03, 32.27it/s]WARNING  [action_state:516] pop empty node_state
8725it [03:04, 44.89it/s]WARNING  [action_state:516] pop empty node_state
8758it [03:04, 46.09it/s]WARNING  [action_state:516] pop empty node_state
8798it [03:05, 40.98it/s]WARNING  [action_state:516] pop empty node_state
WARNING  [action_state:516] pop empty node_state
WARNING  [action_state:516] pop empty node_state
8824it [03:06, 56.24it/s]WARNING  [action_state:516] pop empty node_state
8831it [03:06, 57.43it/s]WARNING  [action_state:516] pop empty node_state
8838it [03:06,

11619it [04:13, 39.83it/s]WARNING  [action_state:516] pop empty node_state
11633it [04:14, 25.18it/s]WARNING  [action_state:516] pop empty node_state
11655it [04:14, 38.22it/s]WARNING  [action_state:516] pop empty node_state
11669it [04:14, 41.34it/s]WARNING  [action_state:516] pop empty node_state
11681it [04:15, 44.33it/s]WARNING  [action_state:516] pop empty node_state
11687it [04:15, 43.41it/s]WARNING  [action_state:516] pop empty node_state
11729it [04:15, 68.99it/s]WARNING  [action_state:516] pop empty node_state
11745it [04:16, 41.02it/s]WARNING  [action_state:516] pop empty node_state
11761it [04:16, 49.63it/s]WARNING  [action_state:516] pop empty node_state
WARNING  [action_state:220] No top node provided
11834it [04:17, 62.08it/s]WARNING  [action_state:516] pop empty node_state
11844it [04:17, 63.73it/s]WARNING  [action_state:516] pop empty node_state
11885it [04:18, 49.86it/s]WARNING  [action_state:516] pop empty node_state
11926it [04:19, 38.48it/s]WARNING  [action_state:51

14071it [05:03, 48.83it/s]WARNING  [action_state:516] pop empty node_state
14078it [05:03, 50.63it/s]WARNING  [action_state:516] pop empty node_state
14092it [05:03, 39.30it/s]WARNING  [action_state:516] pop empty node_state
14133it [05:04, 52.69it/s]WARNING  [action_state:516] pop empty node_state
14149it [05:05, 21.95it/s]WARNING  [action_state:516] pop empty node_state
14163it [05:06, 21.85it/s]WARNING  [action_state:516] pop empty node_state
14179it [05:06, 25.94it/s]WARNING  [action_state:516] pop empty node_state
14252it [05:08, 40.76it/s]WARNING  [action_state:516] pop empty node_state
14262it [05:08, 41.31it/s]WARNING  [action_state:516] pop empty node_state
14324it [05:09, 57.71it/s]WARNING  [action_state:516] pop empty node_state
WARNING  [action_state:516] pop empty node_state
14371it [05:10, 33.00it/s]WARNING  [action_state:516] pop empty node_state
14401it [05:10, 49.51it/s]WARNING  [action_state:516] pop empty node_state
14431it [05:11, 47.95it/s]WARNING  [action_state:51

16955it [06:11, 79.89it/s]WARNING  [action_state:220] No top node provided
16966it [06:11, 46.30it/s]WARNING  [action_state:516] pop empty node_state
17046it [06:13, 47.73it/s]WARNING  [action_state:516] pop empty node_state
WARNING  [action_state:516] pop empty node_state
17095it [06:14, 37.92it/s]WARNING  [action_state:516] pop empty node_state
17193it [06:16, 25.51it/s]WARNING  [action_state:516] pop empty node_state
17216it [06:17, 32.81it/s]WARNING  [action_state:516] pop empty node_state
17285it [06:18, 43.49it/s]WARNING  [action_state:516] pop empty node_state
17347it [06:19, 69.43it/s]WARNING  [action_state:516] pop empty node_state
17395it [06:20, 55.50it/s]WARNING  [action_state:516] pop empty node_state
17405it [06:20, 56.83it/s]WARNING  [action_state:516] pop empty node_state
17420it [06:20, 55.21it/s]WARNING  [action_state:516] pop empty node_state
17446it [06:21, 53.01it/s]WARNING  [action_state:516] pop empty node_state
17467it [06:21, 49.97it/s]WARNING  [action_state:51

19894it [07:17, 61.51it/s]WARNING  [action_state:516] pop empty node_state
19902it [07:17, 56.78it/s]WARNING  [action_state:516] pop empty node_state
19939it [07:17, 66.61it/s]WARNING  [action_state:516] pop empty node_state
WARNING  [action_state:516] pop empty node_state
19954it [07:17, 76.44it/s]WARNING  [action_state:516] pop empty node_state
19977it [07:18, 51.75it/s]WARNING  [action_state:516] pop empty node_state
19987it [07:18, 51.71it/s]WARNING  [action_state:516] pop empty node_state
20000it [07:18, 45.59it/s]

### Test allennlp dataset reader

In [336]:
import torch.optim as optim

from mrp_library.dataset_readers.mrp_jsons import MRPDatasetReader
from allennlp.common.file_utils import cached_path
from allennlp.data.vocabulary import Vocabulary
from allennlp.modules.text_field_embedders import TextFieldEmbedder, BasicTextFieldEmbedder
from allennlp.modules.token_embedders.embedding import Embedding
from allennlp.modules.seq2seq_encoders import Seq2SeqEncoder, PytorchSeq2SeqWrapper
from allennlp.modules.feedforward import FeedForward

from allennlp.training.metrics import CategoricalAccuracy

from allennlp.data.iterators import BucketIterator
from allennlp.training.trainer import Trainer

import json
import logging
from typing import Dict

from allennlp.common.file_utils import cached_path
from allennlp.data.dataset_readers.dataset_reader import DatasetReader
from allennlp.data.fields import LabelField, TextField
from allennlp.data.instance import Instance
from allennlp.data.token_indexers import SingleIdTokenIndexer, TokenIndexer
from allennlp.data.tokenizers import Token, Tokenizer, WordTokenizer
from allennlp.models import Model
from overrides import overrides

In [337]:
from mrp_library.dataset_readers.mrp_jsons_actions import MRPDatasetActionReader

In [338]:
reader = MRPDatasetActionReader()

In [339]:
train_dataset = reader.read(cached_path(allennlp_framework_train_output_file))

0it [00:00, ?it/s]INFO     [mrp_library.dataset_readers.mrp_jsons_actions:139] Reading instances from lines in file at: /data/proj29_ds1/home/slai/mrp2019/allennlp-mrp-json-big-dm-train.jsonl
235it [00:00, 2345.12it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 2)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 3)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 4)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 5)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 6)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 7)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 8)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 9)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] (

8320it [00:02, 3786.20it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 94)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 95)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 96)
8718it [00:02, 3833.25it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 97)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 98)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 99)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 100)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 101)
9103it [00:02, 3792.71it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 102)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 103)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 104)
WARNING  [mrp_library.d

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 188)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 189)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 190)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 191)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 192)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 193)
15566it [00:04, 3721.07it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 194)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 195)
15939it [00:04, 3586.07it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 196)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 197)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 198)
WARNING  [mrp_library.dataset_readers.mrp_

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 283)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 284)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 285)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 286)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 287)
23728it [00:13, 2181.76it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 288)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 289)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 290)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 291)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 292)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 293)
24232it [00:13, 2628.69it/s]WARNING  [mrp_library.dataset_readers.mrp_

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 378)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 379)
31286it [00:15, 3695.33it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 380)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 381)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 382)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 383)
31703it [00:15, 3792.04it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 384)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 385)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 386)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 387)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 388)
WARNING  [mrp_library.dataset_readers.mrp_

...

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 566)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 567)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 568)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 569)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 570)
46831it [00:25, 2758.32it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 571)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 572)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 573)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 574)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 575)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 576)
47308it [00:25, 3155.87it/s]WARNING  [mrp_library.dataset_readers.mrp_

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 661)
52961it [00:27, 3641.23it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 662)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 663)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 664)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 665)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 666)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 667)
53327it [00:27, 3609.91it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 668)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 669)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 670)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 671)
WARNING  [mrp_library.dataset_readers.mrp_

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 755)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 756)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 757)
61422it [00:29, 3853.89it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 758)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 759)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 760)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 761)
61809it [00:29, 3693.23it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 762)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 763)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 764)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 765)
62181it [00:29, 3680.57it/s]WARNING  [mrp_

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 848)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 849)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 850)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 851)
70025it [00:39, 849.43it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 852)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 853)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 854)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 855)
70475it [00:39, 1118.54it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 856)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 857)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 858)
WARNING  [mrp_library.dataset_readers.mrp_j

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 944)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 945)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 946)
76339it [00:40, 3713.86it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 947)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 948)
76721it [00:40, 3726.40it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 949)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 950)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 951)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 952)
77101it [00:40, 3696.21it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 953)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 954)
77532it [00:40

In [340]:
# test_dataset = reader.read(cached_path(allennlp_train_output_file))
test_dataset = reader.read(cached_path(allennlp_framework_test_output_file))

0it [00:00, ?it/s]INFO     [mrp_library.dataset_readers.mrp_jsons_actions:139] Reading instances from lines in file at: /data/proj29_ds1/home/slai/mrp2019/allennlp-mrp-json-big-dm-test.jsonl
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1001)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1002)
202it [00:00, 2018.87it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1003)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1004)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1005)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1006)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1007)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1008)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1009)
WARNING  [mrp_library.dataset_reader

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1092)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1093)
7550it [00:02, 3694.27it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1094)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1095)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1096)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1097)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1098)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1099)
7921it [00:02, 3694.86it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1100)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1101)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1102)
WARNING  [mrp_library.dataset_rea

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1186)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1187)
12930it [00:03, 3434.70it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1188)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1189)
13379it [00:03, 3695.22it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1190)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1191)
13755it [00:03, 3699.56it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1192)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1193)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1194)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1195)
14153it [00:04, 3755.88it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:36

21134it [00:15, 3099.07it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1280)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1281)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1282)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1283)
21536it [00:15, 3266.45it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1284)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1285)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1286)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1287)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1288)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1289)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1290)
WARNING  [mrp_library.dataset_r

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1372)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1373)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1374)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1375)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1376)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1377)
30972it [00:18, 3684.75it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1378)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1379)
31378it [00:18, 3788.86it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1380)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1381)
31775it [00:18, 3817.53it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1382)
WAR

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1465)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1466)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1467)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1468)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1469)
38381it [00:20, 3636.78it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1470)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1471)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1472)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1473)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1474)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1475)
38747it [00:20, 3528.91it/s]WARNING  [mrp_library.dataset_r

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1557)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1558)
48182it [00:32, 643.75it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1559)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1560)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1561)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1562)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1563)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1564)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1565)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1566)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1567)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361]

56428it [00:34, 3951.60it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1651)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1652)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1653)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1654)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1655)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1656)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1657)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1658)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1659)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1660)
56828it [00:34, 3857.77it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1661)
WARNING  [mrp_library.dataset_r

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1745)
63570it [00:36, 3828.83it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1746)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1747)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1748)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1749)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1750)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1751)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1752)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1753)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1754)
63973it [00:36, 3885.59it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1755)
WARNING  [mrp_library.dataset_r

WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1838)
71321it [00:38, 3673.61it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1839)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1840)
71695it [00:38, 3690.80it/s]WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1841)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1842)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1843)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1844)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1845)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1846)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1847)
WARNING  [mrp_library.dataset_readers.mrp_jsons_actions:361] ('error count', 1848)
72065it [00:38, 3658.49it/s]WAR

In [341]:
tests_fixtures_dataset = reader.read(cached_path(allennlp_tests_fixtures_output_file))

0it [00:00, ?it/s]INFO     [mrp_library.dataset_readers.mrp_jsons_actions:139] Reading instances from lines in file at: /data/proj29_ds1/home/slai/mrp2019/src/tests/fixtures/dm-test.jsonl
385it [00:00, 2629.96it/s]


In [342]:
non_padded_namespaces = [
    'action_type',
]
label_fields = [
    'resolved_label_root_label',
    'resolved_label_edge_labels',
]
for framework in frameworks:
    for label_field in label_fields:
        non_padded_namespaces.append('{}_{}'.format(framework, label_field))

In [343]:
non_padded_namespaces

['action_type',
 'ucca_resolved_label_root_label',
 'ucca_resolved_label_edge_labels',
 'psd_resolved_label_root_label',
 'psd_resolved_label_edge_labels',
 'eds_resolved_label_root_label',
 'eds_resolved_label_edge_labels',
 'dm_resolved_label_root_label',
 'dm_resolved_label_edge_labels',
 'amr_resolved_label_root_label',
 'amr_resolved_label_edge_labels']

In [344]:
vocab = Vocabulary.from_instances(
    train_dataset + test_dataset + tests_fixtures_dataset,
    non_padded_namespaces=non_padded_namespaces,
)

INFO     [allennlp.data.vocabulary:396] Fitting token dictionary from dataset.

 63%|██████▎   | 101933/160592 [00:13<00:07, 7506.40it/s]


100%|██████████| 160592/160592 [00:21<00:00, 7408.26it/s]

In [741]:
vocab.print_statistics()

INFO     [allennlp.data.vocabulary:664] Printed vocabulary statistics are only for the part of the vocabulary generated from instances. If vocabulary is constructed by extending saved vocabulary with dataset instances, the directly loaded portion won't be considered here.




----Vocabulary Statistics----


Top 10 most frequent tokens in namespace 'word':
	Token: <START-WORD>		Frequency: 1950440
	Token: ,		Frequency: 617056
	Token: the		Frequency: 588319
	Token: .		Frequency: 426792
	Token: of		Frequency: 292424
	Token: a		Frequency: 278300
	Token: in		Frequency: 207508
	Token: to		Frequency: 191759
	Token: and		Frequency: 186560
	Token: be		Frequency: 162032

Top 10 longest tokens in namespace 'word':
	Token: individual-retirement-account		length: 29	Frequency: 140
	Token: research-and-production		length: 23	Frequency: 156
	Token: electronics-instruments		length: 23	Frequency: 82
	Token: interest-rate-sensitive		length: 23	Frequency: 74
	Token: electronics-instrument		length: 22	Frequency: 82
	Token: weapons-modernization		length: 21	Frequency: 186
	Token: Watergate-beleaguered		length: 21	Frequency: 87
	Token: watergate-beleaguered		length: 21	Frequency: 87
	Token: electronic-publishing		length: 21	Frequency: 84
	Token: Bridgestone/Firestone		length: 21

In [742]:
vocab.get_token_from_index(0, namespace='resolved_label_edge_labels')

'@@PADDING@@'

In [743]:
vocab.get_vocab_size('token_node_label')

11825

In [744]:
vocab.get_vocab_size('ucca_resolved_label_edge_labels')

0

In [745]:
vocab.get_vocab_size('ucca_resolved_label_root_label')

0

In [746]:
vocab.get_vocab_size('dm_resolved_label_edge_labels')

29

In [747]:
vocab.get_vocab_size('dm_resolved_label_root_label')

8198

In [748]:
vocab.get_vocab_size('word')

12071

In [749]:
vocab.get_vocab_size('pos')

65

In [750]:
vocab.get_vocab_size('label')

2

In [751]:
EMBEDDING_DIM = 100
HIDDEN_DIM = 50

### Test model

In [807]:
from mrp_library.models.resolver import Resolver
from mrp_library.iterators.same_instance_type_framework_stack_len_iterator import SameInstanceTypeFrameworkStackLenIterator

from allennlp.nn import InitializerApplicator, RegularizerApplicator, util
from allennlp.nn.activations import Activation
from allennlp.common.params import Params
from allennlp.nn.util import get_text_field_mask, sequence_cross_entropy_with_logits
from allennlp.modules.seq2vec_encoders.pytorch_seq2vec_wrapper import PytorchSeq2VecWrapper
from allennlp.modules.seq2seq_encoders.pytorch_seq2seq_wrapper import PytorchSeq2SeqWrapper

In [808]:
if torch.cuda.is_available() and False:
    cuda_device = args.cuda_device
else:
    cuda_device = -1
cuda_device

-1

In [809]:
def _cuda(variable, cuda_device):
    if cuda_device != -1:
        variable = variable.cuda(cuda_device)
    return variable

In [911]:
field_types = ['word', 'pos', 
               'ucca_word', 'ucca_pos',
               'dm_word', 'dm_pos', 
               'resolved', 'token_node_label', 'token_node_prev_action']

field_type2embedder = {}
field_type2seq2vec_encoder = {}
field_type2seq2seq_encoder = {}

embedding_group2field_types = {
    'word': ['word', 'parse_curr_word', 'parse_prev_word', 'parse_next_word',
             'resolve_dm_word', 'resolve_ucca_word'],
    'pos': ['pos', 'parse_curr_pos', 'parse_prev_pos', 'parse_next_pos',
            'resolve_dm_pos', 'resolve_ucca_pos'],
    'resolved': ['resolved', 'token_node_resolved'],
    'token_node_label': ['token_node_label'],
    'token_node_prev_action': ['action', 'token_node_prev_action'],
    'template': ['template'],
}

seq2vec_group2field_types = {
    'parse_word': ['word', 'parse_curr_word', 'parse_prev_word', 'parse_next_word'],
    'parse_pos': ['pos', 'parse_curr_pos', 'parse_prev_pos', 'parse_next_pos'],
    'resolve_dm_word': ['resolve_dm_word'],
    'resolve_dm_pos': ['resolve_dm_pos'],
    'resolve_ucca_word': ['resolve_ucca_word'],
    'resolve_ucca_pos': ['resolve_ucca_pos'],
    'resolved': ['resolved', 'token_node_resolved'],
    'token_node_label': ['token_node_label'],
    'action': ['action', 'token_node_prev_action'],
}

seq2vec_group2field_types = {
    'parse_word': ['word', 'parse_curr_word', 'parse_prev_word', 'parse_next_word'],
    'parse_pos': ['pos', 'parse_curr_pos', 'parse_prev_pos', 'parse_next_pos'],
    'resolve_dm_word': ['resolve_dm_word'],
    'resolve_dm_pos': ['resolve_dm_pos'],
    'resolve_ucca_word': ['resolve_ucca_word'],
    'resolve_ucca_pos': ['resolve_ucca_pos'],
    'resolved': ['resolved', 'token_node_resolved'],
    'token_node_label': ['token_node_label'],
    'action': ['action', 'token_node_prev_action'],
}

for embedding_group, field_types in embedding_group2field_types.items():
    embedding = _cuda(
        Embedding(
            num_embeddings=vocab.get_vocab_size(embedding_group),
            embedding_dim=EMBEDDING_DIM
        ), cuda_device)
    logger.info((embedding_group, vocab.get_vocab_size(embedding_group)))
    embedder = BasicTextFieldEmbedder({embedding_group: embedding})
    for field_type in field_types:
        field_type2embedder[field_type] = embedder
    
for seq2vec_group, field_types in seq2vec_group2field_types.items():
    seq2vec = PytorchSeq2VecWrapper(
        _cuda(torch.nn.LSTM(EMBEDDING_DIM, HIDDEN_DIM, batch_first=True), cuda_device)
    )
    for field_type in field_types:
        field_type2seq2vec_encoder[field_type] = seq2vec

for seq2seq_group, field_types in seq2vec_group2field_types.items():
    seq2seq = PytorchSeq2SeqWrapper(
        _cuda(torch.nn.LSTM(EMBEDDING_DIM, HIDDEN_DIM, batch_first=True), cuda_device)
    )
    for field_type in field_types:
        field_type2seq2seq_encoder[field_type] = seq2seq

INFO     [__main__:51] ('word', 12071)
INFO     [__main__:51] ('pos', 65)
INFO     [__main__:51] ('resolved', 5)
INFO     [__main__:51] ('token_node_label', 11825)
INFO     [__main__:51] ('token_node_prev_action', 6)
INFO     [__main__:51] ('template', 2)


In [912]:
# word_embedding = Embedding(num_embeddings=vocab.get_vocab_size('word'),
#                             embedding_dim=EMBEDDING_DIM)
# pos_embedding = Embedding(num_embeddings=vocab.get_vocab_size('pos'),
#                             embedding_dim=EMBEDDING_DIM)

# word_embedder = BasicTextFieldEmbedder({
#     "word": word_embedding,
#     "pos": pos_embedding,
# })
# parse_label = {
#     'word': torch.LongTensor(
#         [
#             [ 1,  0,  3,  7,  2,  9,  4],
#             [ 0,  0,  5,  0,  0,  0,  4]
#         ]
#     ),
#     'pos': torch.LongTensor(
#         [
#             [ 1,  0,  3,  7,  2,  9,  4],
#             [ 0,  0,  5,  0,  0,  0,  4]
#         ]
#     )
# }

In [913]:
# embedded_parse_label = word_embedder(parse_label)

In [914]:
# embedded_parse_label.shape

In [915]:
vocab.get_vocab_size('resolved_label_edge_labels')

2

In [916]:
vocab.get_vocab_size('dm_resolved_label_edge_labels')

29

In [917]:
vocab.get_vocab_size('dm_resolved_label_root_label')

8198

In [918]:
action_classifier_params = Params({
  "input_dim": HIDDEN_DIM * 15,
  "num_layers": 2,
  "hidden_dims": [50, 3],
  "activations": ["sigmoid", "linear"],
  "dropout": [0.0, 0.0]
})

action_num_pop_classifier_params = Params({
  "input_dim": HIDDEN_DIM * 2,
  "num_layers": 2,
  "hidden_dims": [50, 1],
  "activations": ["sigmoid", "linear"],
  "dropout": [0.0, 0.0]
})

framework2field_type2feedforward_params = {
    'dm':{
        'child_edges': Params({
            "input_dim": HIDDEN_DIM * 4,
            "num_layers": 2,
            "hidden_dims": [100, vocab.get_vocab_size('dm_resolved_label_edge_labels')],
            "activations": ["sigmoid", "linear"],
            "dropout": [0.0, 0.0]
        }),
        'root_label': Params({
            "input_dim": EMBEDDING_DIM * 4,
            "num_layers": 2,
            "hidden_dims": [100, vocab.get_vocab_size('dm_resolved_label_root_label')],
            "activations": ["sigmoid", "linear"],
            "dropout": [0.0, 0.0]
        }),
    },
    'ucca':{
        'child_edges': Params({
            "input_dim": HIDDEN_DIM * 4,
            "num_layers": 2,
            "hidden_dims": [100, vocab.get_vocab_size('ucca_resolved_label_edge_labels')],
            "activations": ["sigmoid", "linear"],
            "dropout": [0.0, 0.0]
        }),
        'root_label': Params({
            "input_dim": EMBEDDING_DIM * 4,
            "num_layers": 2,
            "hidden_dims": [100, vocab.get_vocab_size('ucca_resolved_label_root_label')],
            "activations": ["sigmoid", "linear"],
            "dropout": [0.0, 0.0]
        }),
    },
}

In [919]:
action_classifier_feedforward = FeedForward.from_params(action_classifier_params)
action_classifier_feedforward = _cuda(action_classifier_feedforward, cuda_device)

action_num_pop_classifier_feedforward = FeedForward.from_params(action_num_pop_classifier_params)
action_num_pop_classifier_feedforward = _cuda(action_num_pop_classifier_feedforward, cuda_device)

INFO     [allennlp.common.from_params:340] instantiating class <class 'allennlp.modules.feedforward.FeedForward'> from params {'input_dim': 750, 'num_layers': 2, 'hidden_dims': [50, 3], 'activations': ['sigmoid', 'linear'], 'dropout': [0.0, 0.0]} and extras set()
INFO     [allennlp.common.params:252] input_dim = 750
INFO     [allennlp.common.params:252] num_layers = 2
INFO     [allennlp.common.params:252] hidden_dims = [50, 3]
INFO     [allennlp.common.params:252] hidden_dims = [50, 3]
INFO     [allennlp.common.params:252] activations = ['sigmoid', 'linear']
INFO     [allennlp.common.from_params:340] instantiating class <class 'allennlp.nn.activations.Activation'> from params ['sigmoid', 'linear'] and extras set()
INFO     [allennlp.common.params:252] activations = ['sigmoid', 'linear']
INFO     [allennlp.common.from_params:340] instantiating class <class 'allennlp.nn.activations.Activation'> from params sigmoid and extras set()
INFO     [allennlp.common.params:252] type = sigmoid
INFO

In [920]:
framework2field_type2feedforward = {}

for framework, field_type2feedforward_params in framework2field_type2feedforward_params.items():
    framework2field_type2feedforward[framework] = {}
    for field_type, feedforward_params in field_type2feedforward_params.items():
        feedforward_classifier = FeedForward.from_params(
            feedforward_params)
        feedforward_classifier = _cuda(feedforward_classifier, cuda_device)
        framework2field_type2feedforward[framework][field_type] = feedforward_classifier
    framework2field_type2feedforward[framework] = torch.nn.ModuleDict(framework2field_type2feedforward[framework])

framework2field_type2feedforward = torch.nn.ModuleDict(framework2field_type2feedforward)

INFO     [allennlp.common.from_params:340] instantiating class <class 'allennlp.modules.feedforward.FeedForward'> from params {'input_dim': 200, 'num_layers': 2, 'hidden_dims': [100, 29], 'activations': ['sigmoid', 'linear'], 'dropout': [0.0, 0.0]} and extras set()
INFO     [allennlp.common.params:252] input_dim = 200
INFO     [allennlp.common.params:252] num_layers = 2
INFO     [allennlp.common.params:252] hidden_dims = [100, 29]
INFO     [allennlp.common.params:252] hidden_dims = [100, 29]
INFO     [allennlp.common.params:252] activations = ['sigmoid', 'linear']
INFO     [allennlp.common.from_params:340] instantiating class <class 'allennlp.nn.activations.Activation'> from params ['sigmoid', 'linear'] and extras set()
INFO     [allennlp.common.params:252] activations = ['sigmoid', 'linear']
INFO     [allennlp.common.from_params:340] instantiating class <class 'allennlp.nn.activations.Activation'> from params sigmoid and extras set()
INFO     [allennlp.common.params:252] type = sigmoi

In [921]:
field_type = 'word'

In [922]:
field_type2embedder.keys()

dict_keys(['word', 'parse_curr_word', 'parse_prev_word', 'parse_next_word', 'resolve_dm_word', 'resolve_ucca_word', 'pos', 'parse_curr_pos', 'parse_prev_pos', 'parse_next_pos', 'resolve_dm_pos', 'resolve_ucca_pos', 'resolved', 'token_node_resolved', 'token_node_label', 'action', 'token_node_prev_action', 'template'])

In [923]:
parse_label = {
    field_type: _cuda(
        torch.LongTensor(
            [
                [ 1,  0,  3,  7,  2,  9,  4],
                [ 0,  0,  5,  0,  0,  0,  4]
            ]
        ),
        cuda_device
    )
}
embedded_parse_label = field_type2embedder[field_type](parse_label)

In [924]:
feature_mask = util.get_text_field_mask(parse_label)

In [925]:
seq2vec_encoder = field_type2seq2vec_encoder[field_type]

In [926]:
encoded_feature = seq2vec_encoder(embedded_parse_label, feature_mask)

In [927]:
encoded_features = [encoded_feature] * 15

In [928]:
# torch.cat(encoded_features, dim=-1)

In [929]:
actions

[(0, None),
 (1,
  (1,
   0,
   {'id': 0,
    'anchors': [{'from': 0, 'to': 2}],
    'label': 'In',
    'propagate_label': 'R'},
   [[]])),
 (0, None),
 (1,
  (1,
   0,
   {'id': 1,
    'anchors': [{'from': 3, 'to': 6}],
    'label': 'the',
    'propagate_label': 'E'},
   [[]])),
 (0, None),
 (1,
  (1,
   0,
   {'id': 2,
    'anchors': [{'from': 7, 'to': 12}],
    'label': 'final',
    'propagate_label': 'E'},
   [[]])),
 (0, None),
 (1,
  (1,
   0,
   {'id': 3,
    'anchors': [{'from': 13, 'to': 19}],
    'label': 'minute',
    'propagate_label': 'C'},
   [[]])),
 (1,
  (4,
   3,
   {'id': 31, 'propagate_label': 'E'},
   [[{'source': 31,
      'target': 0,
      'label': 'R',
      'id': 31,
      'parent': 31,
      'child': 0}],
    [{'source': 31,
      'target': 1,
      'label': 'E',
      'id': 28,
      'parent': 31,
      'child': 1}],
    [{'source': 31,
      'target': 2,
      'label': 'E',
      'id': 21,
      'parent': 31,
      'child': 2}],
    [{'source': 31,
      't

In [930]:
logits = action_classifier_feedforward(torch.cat(encoded_features, dim=-1))

In [931]:
logits.shape

torch.Size([2, 3])

In [932]:
label = torch.tensor([1, 0])

In [933]:
# loss_func = torch.nn.CrossEntropyLoss()
# loss = loss_func(logits, label)

In [934]:
from mrp_library.models.resolver import Resolver
from mrp_library.iterators.same_instance_type_framework_stack_len_iterator import SameInstanceTypeFrameworkStackLenIterator


In [935]:
if torch.cuda.is_available() and False:
    cuda_device = args.cuda_device
    model = Resolver(
        cuda_device=cuda_device,
        vocab=vocab,
        field_type2embedder=field_type2embedder,
        field_type2seq2vec_encoder=field_type2seq2vec_encoder,
        field_type2seq2seq_encoder=field_type2seq2seq_encoder,
        action_classifier_feedforward=action_classifier_feedforward,
        action_num_pop_classifier_feedforward=action_num_pop_classifier_feedforward,
        framework2field_type2feedforward=framework2field_type2feedforward,
    )
    model = model.cuda(cuda_device)
else:
    cuda_device = -1
    model = Resolver(
        cuda_device=cuda_device,
        vocab=vocab,
        field_type2embedder=field_type2embedder,
        field_type2seq2vec_encoder=field_type2seq2vec_encoder,
        field_type2seq2seq_encoder=field_type2seq2seq_encoder,
        action_classifier_feedforward=action_classifier_feedforward,
        action_num_pop_classifier_feedforward=action_num_pop_classifier_feedforward,
        framework2field_type2feedforward=framework2field_type2feedforward,
    )

# iterator = SameInstanceTypeFrameworkIterator(
#     shuffle=True,
#     batch_size=100, 
#     sorting_keys=[("token_node_resolveds", "num_tokens")],
# )
iterator = SameInstanceTypeFrameworkStackLenIterator(
    shuffle=True,
    batch_size=100, 
    sorting_keys=[("token_node_resolveds", "num_tokens")],
)
iterator.index_with(vocab)

optimizer = optim.SGD(model.parameters(), lr=0.1)

INFO     [allennlp.nn.initializers:293] Initializing parameters
INFO     [allennlp.nn.initializers:309] Done initializing parameters; the following parameters are using their default initialization from their code
INFO     [allennlp.nn.initializers:314]    action_classifier_feedforward._linear_layers.0.bias
INFO     [allennlp.nn.initializers:314]    action_classifier_feedforward._linear_layers.0.weight
INFO     [allennlp.nn.initializers:314]    action_classifier_feedforward._linear_layers.1.bias
INFO     [allennlp.nn.initializers:314]    action_classifier_feedforward._linear_layers.1.weight
INFO     [allennlp.nn.initializers:314]    action_num_pop_classifier_feedforward._linear_layers.0.bias
INFO     [allennlp.nn.initializers:314]    action_num_pop_classifier_feedforward._linear_layers.0.weight
INFO     [allennlp.nn.initializers:314]    action_num_pop_classifier_feedforward._linear_layers.1.bias
INFO     [allennlp.nn.initializers:314]    action_num_pop_classifier_feedforward._linear_la

INFO     [allennlp.nn.initializers:314]    field_type2seq2vec_encoder.resolve_ucca_word._module.weight_ih_l0
INFO     [allennlp.nn.initializers:314]    field_type2seq2vec_encoder.resolved._module.bias_hh_l0
INFO     [allennlp.nn.initializers:314]    field_type2seq2vec_encoder.resolved._module.bias_ih_l0
INFO     [allennlp.nn.initializers:314]    field_type2seq2vec_encoder.resolved._module.weight_hh_l0
INFO     [allennlp.nn.initializers:314]    field_type2seq2vec_encoder.resolved._module.weight_ih_l0
INFO     [allennlp.nn.initializers:314]    field_type2seq2vec_encoder.token_node_label._module.bias_hh_l0
INFO     [allennlp.nn.initializers:314]    field_type2seq2vec_encoder.token_node_label._module.bias_ih_l0
INFO     [allennlp.nn.initializers:314]    field_type2seq2vec_encoder.token_node_label._module.weight_hh_l0
INFO     [allennlp.nn.initializers:314]    field_type2seq2vec_encoder.token_node_label._module.weight_ih_l0
INFO     [allennlp.nn.initializers:314]    framework2field_type2fee

In [936]:
cuda_device

-1

In [937]:
model.resolve_tensor

tensor(1)

In [938]:
# list(model.named_parameters())

In [939]:
trainer = Trainer(
    model=model,
    optimizer=optimizer,
    iterator=iterator,
    train_dataset=train_dataset,
    validation_dataset=test_dataset,
#     train_dataset=train_dataset,
#     validation_dataset=train_dataset,
    patience=10,
    num_epochs=20,
    cuda_device=cuda_device
)

In [940]:
action_logits = torch.tensor([[-2.2126,  2.6022, -1.1655],
        [ 4.7340, -1.9992, -3.4521],
        [-1.9665,  2.4100, -1.2047],
        [-2.1353,  2.4847, -1.1260],
        [ 4.7492, -2.0234, -3.4460],
        [-1.4369,  1.9822, -1.2885],
        [ 1.0337,  0.3599, -2.0420],
        [ 5.0974, -2.3380, -3.4647],
        [ 5.4187, -2.4720, -3.6469],
        [-3.4045,  2.4903,  0.0773],
        [ 0.6384,  0.6764, -1.9942],
        [-2.2904,  2.7170, -1.2016],
        [ 4.6333, -1.9474, -3.4113],
        [-2.0811,  2.5367, -1.2174],
        [ 5.1840, -2.7536, -3.1499],
        [ 4.7421, -2.0138, -3.4485],
        [ 5.1121, -2.2290, -3.5999],
        [ 0.1843,  0.8324, -1.6990],
        [ 5.3854, -2.4593, -3.6309],
        [ 0.0324,  0.6715, -1.4173]])
action_logits = _cuda(action_logits, cuda_device)

action_type = torch.tensor([0, 2, 2, 1, 1, 0, 1, 2, 1, 2, 1, 1, 1, 0, 0, 1, 0, 0, 1, 0])
action_type = _cuda(action_type, cuda_device)

In [941]:
action_probs, action_preds = action_logits.max(1)
action_resolve_preds = action_preds.eq_(model.resolve_tensor)

In [942]:
iter([1, 2, 3, 4])

In [943]:
defaultdict(lambda: defaultdict(dict))

defaultdict(<function __main__.<lambda>()>, {})

In [944]:
(action_resolve_preds, action_type, action_resolve_preds.eq(action_type))

(tensor([1, 0, 1, 1, 0, 1, 0, 0, 0, 1, 1, 1, 0, 1, 0, 0, 0, 1, 0, 1]),
 tensor([0, 2, 2, 1, 1, 0, 1, 2, 1, 2, 1, 1, 1, 0, 0, 1, 0, 0, 1, 0]),
 tensor([0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 0],
        dtype=torch.uint8))

In [945]:
action_resolve_preds.unsqueeze(-1).float() * action_logits

tensor([[-2.2126,  2.6022, -1.1655],
        [ 0.0000, -0.0000, -0.0000],
        [-1.9665,  2.4100, -1.2047],
        [-2.1353,  2.4847, -1.1260],
        [ 0.0000, -0.0000, -0.0000],
        [-1.4369,  1.9822, -1.2885],
        [ 0.0000,  0.0000, -0.0000],
        [ 0.0000, -0.0000, -0.0000],
        [ 0.0000, -0.0000, -0.0000],
        [-3.4045,  2.4903,  0.0773],
        [ 0.6384,  0.6764, -1.9942],
        [-2.2904,  2.7170, -1.2016],
        [ 0.0000, -0.0000, -0.0000],
        [-2.0811,  2.5367, -1.2174],
        [ 0.0000, -0.0000, -0.0000],
        [ 0.0000, -0.0000, -0.0000],
        [ 0.0000, -0.0000, -0.0000],
        [ 0.1843,  0.8324, -1.6990],
        [ 0.0000, -0.0000, -0.0000],
        [ 0.0324,  0.6715, -1.4173]])

In [946]:
embedded_fields = torch.ones(99, 62, 100)

In [947]:
embedded_fields.size()

torch.Size([99, 62, 100])

In [948]:
# embedded_fields

In [949]:
root_position_logits = torch.tensor([[0.1722, 0.1723, 0.1720, 0.1721, 0.1721, 0.1719, 0.1717, 0.1719, 0.1717,
         0.1716, 0.1719, 0.1717, 0.1716, 0.1718, 0.1719, 0.1718, 0.1719, 0.1717,
         0.1720, 0.1720, 0.1722, 0.1722, 0.1719, 0.1721, 0.1718, 0.1717, 0.1719,
         0.1717, 0.1720, 0.1715, 0.1718],
        [0.1722, 0.1723, 0.1720, 0.1721, 0.1721, 0.1719, 0.1717, 0.1719, 0.1717,
         0.1716, 0.1719, 0.1717, 0.1716, 0.1718, 0.1719, 0.1718, 0.1719, 0.1717,
         0.1720, 0.1720, 0.1722, 0.1722, 0.1719, 0.1721, 0.1718, 0.1717, 0.1719,
         0.1717, 0.1716, 0.1719, 0.1708],
        [0.1722, 0.1723, 0.1720, 0.1721, 0.1721, 0.1719, 0.1717, 0.1719, 0.1717,
         0.1716, 0.1719, 0.1717, 0.1716, 0.1718, 0.1719, 0.1718, 0.1719, 0.1717,
         0.1720, 0.1720, 0.1722, 0.1722, 0.1719, 0.1721, 0.1718, 0.1717, 0.1719,
         0.1717, 0.1720, 0.1715, 0.1717],
        [0.1722, 0.1723, 0.1720, 0.1721, 0.1721, 0.1719, 0.1717, 0.1719, 0.1717,
         0.1716, 0.1719, 0.1717, 0.1716, 0.1718, 0.1719, 0.1718, 0.1719, 0.1717,
         0.1720, 0.1720, 0.1722, 0.1722, 0.1719, 0.1721, 0.1718, 0.1717, 0.1719,
         0.1717, 0.1716, 0.1719, 0.1717],
        [0.1722, 0.1723, 0.1720, 0.1721, 0.1721, 0.1719, 0.1717, 0.1719, 0.1717,
         0.1716, 0.1719, 0.1717, 0.1716, 0.1718, 0.1719, 0.1718, 0.1719, 0.1717,
         0.1720, 0.1720, 0.1722, 0.1722, 0.1719, 0.1721, 0.1718, 0.1717, 0.1719,
         0.1717, 0.1720, 0.1715, 0.1709]])

In [950]:
root_position_logits.shape
root_position = torch.tensor([ 2,  0, -1,  1,  0])
mask = root_position.eq(torch.tensor(-1)).unsqueeze(-1).expand_as(root_position_logits)
mask = root_position.gt(-1)
masked_root_position_logits = root_position_logits * mask.float().unsqueeze(-1).expand_as(root_position_logits)
loss = torch.nn.CrossEntropyLoss()
inp = root_position_logits
# crossEntropy = -torch.log(torch.gather(inp, 1, root_position.view(-1, 1)))
root_position
# root_position.eq(torch.tensor(-2)).expand_as(root_position_logits)

tensor([ 2,  0, -1,  1,  0])

In [951]:
a = [1, 2]

In [952]:
d = {'b': a, 'c': a}

In [953]:
a.append(3)

In [954]:
d

{'b': [1, 2, 3], 'c': [1, 2, 3]}

In [955]:
masked_root_position_logits.shape

torch.Size([5, 31])

In [956]:
root_position.shape

torch.Size([5])

In [957]:
torch.ones(2, 3, 47).transpose(1, 2).shape

torch.Size([2, 47, 3])

In [958]:
[dim for dim in torch.tensor([[]]).size()]

[1, 0]

In [959]:
torch.tensor([[]]).shape[1]

0

In [ ]:
trainer.train()

INFO     [allennlp.training.trainer:465] Beginning training.
INFO     [allennlp.training.trainer:281] Epoch 0/19
INFO     [allennlp.training.trainer:283] Peak CPU memory usage MB: 13821.404
INFO     [allennlp.training.trainer:287] GPU 0 memory usage MB: 10
INFO     [allennlp.training.trainer:287] GPU 1 memory usage MB: 11
INFO     [allennlp.training.trainer:287] GPU 2 memory usage MB: 11
INFO     [allennlp.training.trainer:287] GPU 3 memory usage MB: 10
INFO     [allennlp.training.trainer:287] GPU 4 memory usage MB: 11
INFO     [allennlp.training.trainer:287] GPU 5 memory usage MB: 10
INFO     [allennlp.training.trainer:287] GPU 6 memory usage MB: 11
INFO     [allennlp.training.trainer:287] GPU 7 memory usage MB: 10
INFO     [allennlp.training.trainer:311] Training

  0%|          | 0/810 [00:00<?, ?it/s]
action_type_accuracy: 0.4546, action_num_pop_accuracy: 0.2043, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 2.6621 ||:   0%|          | 1/810 [00:00<13:0

action_type_accuracy: 0.4642, action_num_pop_accuracy: 0.2045, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 2.5229 ||:   5%|▍         | 37/810 [00:10<02:51,  4.51it/s]
action_type_accuracy: 0.4643, action_num_pop_accuracy: 0.2045, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 2.4843 ||:   5%|▍         | 38/810 [00:10<02:33,  5.03it/s]
action_type_accuracy: 0.4646, action_num_pop_accuracy: 0.2045, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 2.4439 ||:   5%|▍         | 39/810 [00:10<02:30,  5.13it/s]
action_type_accuracy: 0.4645, action_num_pop_accuracy: 0.2045, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 2.4102 ||:   5%|▍         | 40/810 [00:11<02:21,  5.44it/s]
action_type_accuracy: 0.4647, action_num_pop_accuracy: 0.2045, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 2.3754 ||:   5%|▌         | 41/810 [00:11<02:17,  5.59it/s]
action_typ

action_type_accuracy: 0.4676, action_num_pop_accuracy: 0.2045, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.7167 ||:  10%|▉         | 77/810 [00:16<01:50,  6.65it/s]
action_type_accuracy: 0.4678, action_num_pop_accuracy: 0.2045, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.7060 ||:  10%|▉         | 78/810 [00:17<01:54,  6.38it/s]
action_type_accuracy: 0.4679, action_num_pop_accuracy: 0.2045, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.6967 ||:  10%|▉         | 79/810 [00:17<02:01,  6.03it/s]
action_type_accuracy: 0.4680, action_num_pop_accuracy: 0.2045, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.6872 ||:  10%|▉         | 80/810 [00:17<01:59,  6.09it/s]
action_type_accuracy: 0.4681, action_num_pop_accuracy: 0.2045, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.6788 ||:  10%|█         | 81/810 [00:17<01:58,  6.14it/s]
action_typ

action_type_accuracy: 0.4725, action_num_pop_accuracy: 0.2043, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.5762 ||:  15%|█▍        | 118/810 [00:24<02:39,  4.33it/s]
action_type_accuracy: 0.4727, action_num_pop_accuracy: 0.2044, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.5760 ||:  15%|█▍        | 119/810 [00:24<02:51,  4.02it/s]
action_type_accuracy: 0.4729, action_num_pop_accuracy: 0.2043, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.5760 ||:  15%|█▍        | 120/810 [00:25<02:50,  4.04it/s]
action_type_accuracy: 0.4730, action_num_pop_accuracy: 0.2045, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.5759 ||:  15%|█▍        | 121/810 [00:25<02:57,  3.87it/s]
action_type_accuracy: 0.4731, action_num_pop_accuracy: 0.2044, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.5765 ||:  15%|█▌        | 122/810 [00:25<02:47,  4.12it/s]
actio

action_type_accuracy: 0.4795, action_num_pop_accuracy: 0.2051, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.5787 ||:  20%|█▉        | 158/810 [00:34<02:52,  3.77it/s]
action_type_accuracy: 0.4795, action_num_pop_accuracy: 0.2050, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2786, loss: 1.5796 ||:  20%|█▉        | 159/810 [00:34<02:44,  3.95it/s]
action_type_accuracy: 0.4795, action_num_pop_accuracy: 0.2050, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2784, loss: 1.5752 ||:  20%|█▉        | 160/810 [00:34<02:32,  4.26it/s]
action_type_accuracy: 0.4795, action_num_pop_accuracy: 0.2050, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2782, loss: 1.5698 ||:  20%|█▉        | 161/810 [00:34<02:08,  5.06it/s]
action_type_accuracy: 0.4795, action_num_pop_accuracy: 0.2050, root_label_type_accuracy: 0.2663, child_edges_type_accuracy: 0.2773, loss: 1.5631 ||:  20%|██        | 162/810 [00:35<02:22,  4.55it/s]
actio

...

action_type_accuracy: 0.8114, action_num_pop_accuracy: 0.1391, root_label_type_accuracy: 0.0000, child_edges_type_accuracy: 0.0745, loss: 1.6627 ||:  26%|██▌       | 203/793 [00:20<00:37, 15.62it/s]
action_type_accuracy: 0.8116, action_num_pop_accuracy: 0.1391, root_label_type_accuracy: 0.0000, child_edges_type_accuracy: 0.0745, loss: 1.6509 ||:  26%|██▌       | 205/793 [00:21<00:37, 15.74it/s]
action_type_accuracy: 0.8117, action_num_pop_accuracy: 0.1391, root_label_type_accuracy: 0.0000, child_edges_type_accuracy: 0.0745, loss: 1.6405 ||:  26%|██▌       | 207/793 [00:21<00:36, 15.87it/s]
action_type_accuracy: 0.8125, action_num_pop_accuracy: 0.1391, root_label_type_accuracy: 0.0000, child_edges_type_accuracy: 0.0745, loss: 1.6284 ||:  26%|██▋       | 209/793 [00:21<00:36, 15.88it/s]
action_type_accuracy: 0.8129, action_num_pop_accuracy: 0.1391, root_label_type_accuracy: 0.0000, child_edges_type_accuracy: 0.0745, loss: 1.6165 ||:  27%|██▋       | 211/793 [00:21<00:36, 15.99it/s]
actio

action_type_accuracy: 0.8175, action_num_pop_accuracy: 0.1389, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.0698, loss: 1.5158 ||:  35%|███▌      | 281/793 [00:27<01:18,  6.52it/s]
action_type_accuracy: 0.8175, action_num_pop_accuracy: 0.1389, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.0717, loss: 1.5112 ||:  36%|███▌      | 282/793 [00:27<01:29,  5.71it/s]
action_type_accuracy: 0.8175, action_num_pop_accuracy: 0.1389, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.0704, loss: 1.5029 ||:  36%|███▌      | 284/793 [00:28<01:27,  5.84it/s]
action_type_accuracy: 0.8175, action_num_pop_accuracy: 0.1389, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.0716, loss: 1.4943 ||:  36%|███▌      | 286/793 [00:28<01:27,  5.82it/s]
action_type_accuracy: 0.8175, action_num_pop_accuracy: 0.1389, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.0718, loss: 1.4870 ||:  36%|███▋      | 288/793 [00:28<01:08,  7.39it/s]
actio

action_type_accuracy: 0.8174, action_num_pop_accuracy: 0.1748, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.0718, loss: 1.4860 ||:  41%|████▏     | 329/793 [00:33<00:49,  9.36it/s]
action_type_accuracy: 0.8175, action_num_pop_accuracy: 0.1755, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.0718, loss: 1.4860 ||:  42%|████▏     | 330/793 [00:33<00:48,  9.54it/s]
action_type_accuracy: 0.8176, action_num_pop_accuracy: 0.1764, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.0718, loss: 1.4858 ||:  42%|████▏     | 331/793 [00:33<00:49,  9.25it/s]
action_type_accuracy: 0.8176, action_num_pop_accuracy: 0.1771, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.0718, loss: 1.4857 ||:  42%|████▏     | 332/793 [00:33<00:52,  8.76it/s]
action_type_accuracy: 0.8176, action_num_pop_accuracy: 0.1775, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.0718, loss: 1.4859 ||:  42%|████▏     | 333/793 [00:34<00:55,  8.29it/s]
actio

action_type_accuracy: 0.8177, action_num_pop_accuracy: 0.1939, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.1265, loss: 1.4065 ||:  49%|████▉     | 388/793 [00:38<00:30, 13.15it/s]
action_type_accuracy: 0.8177, action_num_pop_accuracy: 0.1939, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.1252, loss: 1.4012 ||:  49%|████▉     | 390/793 [00:39<00:39, 10.08it/s]
action_type_accuracy: 0.8177, action_num_pop_accuracy: 0.1939, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.1289, loss: 1.3965 ||:  49%|████▉     | 392/793 [00:39<00:35, 11.26it/s]
action_type_accuracy: 0.8177, action_num_pop_accuracy: 0.1939, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.1323, loss: 1.3929 ||:  50%|████▉     | 394/793 [00:39<00:31, 12.47it/s]
action_type_accuracy: 0.8177, action_num_pop_accuracy: 0.1939, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.1358, loss: 1.3893 ||:  50%|████▉     | 396/793 [00:39<00:29, 13.50it/s]
actio

action_type_accuracy: 0.8268, action_num_pop_accuracy: 0.1919, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.1932, loss: 1.2882 ||:  59%|█████▊    | 465/793 [00:45<00:23, 14.16it/s]
action_type_accuracy: 0.8268, action_num_pop_accuracy: 0.1919, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.1953, loss: 1.2857 ||:  59%|█████▉    | 467/793 [00:45<00:22, 14.43it/s]
action_type_accuracy: 0.8268, action_num_pop_accuracy: 0.1919, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.1949, loss: 1.2825 ||:  59%|█████▉    | 469/793 [00:46<00:21, 14.84it/s]
action_type_accuracy: 0.8268, action_num_pop_accuracy: 0.1919, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.1921, loss: 1.2787 ||:  59%|█████▉    | 471/793 [00:46<00:21, 14.83it/s]
action_type_accuracy: 0.8268, action_num_pop_accuracy: 0.1919, root_label_type_accuracy: 0.2665, child_edges_type_accuracy: 0.1894, loss: 1.2748 ||:  60%|█████▉    | 473/793 [00:46<00:21, 14.79it/s]
actio

In [ ]:
torch.ones(98, 29, 5).view(-1, 29).shape

In [ ]:
vocab.get_token_index()

In [ ]:
vocab.get_token_from_index(2, namespace='action_type')

In [ ]:
vocab.get_token_from_index(1, namespace='resolve_label_root_label')

In [ ]:
token_state = [[26, True, 'H', [[23, True, 'A', [[0, True, 'E', [[0, False, 'The', []]]], [1, True, 'C', [[1, False, 'Lakers', []]]]]], [2, True, 'P', [[2, False, 'advanced', []]]], [25, True, 'A', [[3, True, 'R', [[3, False, 'through', []]]], [4, True, 'E', [[4, False, 'the', []]]], [24, True, 'P', [[5, True, 'T', [[5, False, '1982', []]]], [6, True, 'C', [[6, False, 'playoffs', []]]]]]]]]], [7, True, 'L', [[7, False, 'and', []]]], [8, True, 'P', [[8, False, 'faced', []]]], [9, True, 'A', [[9, False, 'Philadelphia', []]]], [27, True, 'D', [[10, True, 'R', [[10, False, 'for', []]]], [11, True, 'E', [[11, False, 'the', []]]], [12, True, 'Q', [[12, False, 'second', []]]], [13, True, 'C', [[13, False, 'time', []]]]]], [14, True, 'R', [[14, False, 'in', []]]], [15, True, 'Q', [[15, False, 'three', []]]], [16, False, 'years', []]]

In [ ]:
pprint.pprint(token_state)

In [ ]:
vocab.get_token_from_index(0, namespace='labels')

In [ ]:
vocab.get_token_index('RESOLVE')

In [ ]:
vocab.get_token_from_index(3, namespace='resolved')

In [ ]:
vocab.get_token_from_index(5, namespace='token_node_prev_action')